Copyright **`(c)`** 2023 Giovanni Squillero `<giovanni.squillero@polito.it>`  
[`https://github.com/squillero/computational-intelligence`](https://github.com/squillero/computational-intelligence)  
Free for personal or classroom use; see [`LICENSE.md`](https://github.com/squillero/computational-intelligence/blob/master/LICENSE.md) for details.  

In [29]:
from random import random, choice, randint
from functools import reduce
from collections import namedtuple
from dataclasses import dataclass
from copy import copy

from pprint import pprint

import numpy as np

In [30]:
PROBLEM_SIZE = 10
NUM_SETS = 50
SETS = tuple(np.array([random() < 0.2 for _ in range(PROBLEM_SIZE)]) for _ in range(NUM_SETS))
State = namedtuple('State', ['taken', 'not_taken'])
SETS

(array([False, False, False, False, False, False, False, False, False,
        False]),
 array([False,  True, False,  True,  True, False, False, False, False,
        False]),
 array([False, False, False,  True, False, False, False,  True, False,
         True]),
 array([False, False, False, False, False,  True, False, False,  True,
        False]),
 array([False,  True, False,  True, False, False, False, False, False,
        False]),
 array([False, False, False,  True, False, False, False, False, False,
        False]),
 array([False,  True, False, False, False, False, False, False,  True,
        False]),
 array([False,  True,  True, False,  True, False, False, False, False,
         True]),
 array([False, False, False, False, False, False, False, False, False,
        False]),
 array([False, False, False, False, False, False, False, False,  True,
        False]),
 array([False, False, False, False,  True,  True, False, False,  True,
        False]),
 array([False, False,  True,  Tr

In [31]:
def fitness1(state):
    cost = sum(state)
    valid = np.all(
        reduce(
            np.logical_or,
            [SETS[i] for i, t in enumerate(state) if t],
            np.array([False for _ in range(PROBLEM_SIZE)]),
        )
    )
    return valid, -cost

def fitness2(state):
    cost = sum(state)
    valid = np.sum(
        reduce(
            np.logical_or,
            [SETS[i] for i, t in enumerate(state) if t],
            np.array([False for _ in range(PROBLEM_SIZE)]),
        )
    )
    return valid, -cost

fitness = fitness2

In [32]:
POPULATION_SIZE = 30
OFFSPRING_SIZE = 20
TOURNAMENT_SIZE = 2
MUTATION_PROBABILITY = .15

In [33]:
@dataclass
class Individual:
    fitness: tuple
    genotype: list[bool]

def select_parent(pop):
    pool = [choice(pop) for _ in range(TOURNAMENT_SIZE)] # choose 2 elem from population
    champion = max(pool, key=lambda i: i.fitness) # get element with better fitness
    return champion

def mutate(ind: Individual) -> Individual:
    offspring = copy(ind)
    pos = randint(0, PROBLEM_SIZE-1) # maybe BUG: NUM_SETS -> PROBLEM_SIZE
    offspring.genotype[pos] = not offspring.genotype[pos] # mutation on a single element of this configuration
    offspring.fitness = None
    return offspring

def one_cut_xover(ind1: Individual, ind2: Individual) -> Individual:
    cut_point = randint(0, PROBLEM_SIZE-1) # maybe BUG: NUM_SETS -> PROBLEM_SIZE
    offspring = Individual(fitness=None, # generate a new individual made of splits of the 2 individuals
                           genotype=ind1.genotype[:cut_point] + ind2.genotype[cut_point:])
    assert len(offspring.genotype) == PROBLEM_SIZE # maybe BUG: NUM_SETS -> PROBLEM_SIZE
    return offspring

In [34]:
population = [
    Individual(
        genotype=[choice((False, False)) for _ in range(PROBLEM_SIZE)], # maybe BUG: NUM_SETS -> PROBLEM_SIZE
        fitness=None,
    )
    for _ in range(POPULATION_SIZE)
]

for i in population:
    i.fitness = fitness(i.genotype)

In [37]:
for idx, generation in enumerate(range(100)):
    print(f'-------------- GENERATION {idx+1} --------------')
    offspring = list()
    for counter in range(OFFSPRING_SIZE):
        if random() < MUTATION_PROBABILITY:  # self-adapt mutation probability
            # mutation  # add more clever mutations
            print('MUTATION:')
            p = select_parent(population)
            print(f'parent {p.genotype}', end ='')
            o = mutate(p)
            print(f' -> {o.genotype}')
        else:
            # xover # add more xovers
            print('CUT XOVER:')
            p1 = select_parent(population)
            p2 = select_parent(population)
            o = one_cut_xover(p1, p2)
            print(f'{p1.genotype} + {p2.genotype} -> {o.genotype}')
        offspring.append(o)
        print()

    for i in offspring:
        i.fitness = fitness(i.genotype)
    population.extend(offspring) # add new individuals to population
    population.sort(key=lambda i: i.fitness, reverse=True)
    population = population[:POPULATION_SIZE] # always keep the first POPULATION_SIZE best individuals

    print()
    print(f'Pouplation at end of generation {idx+1}:')
    for idividual in population:
        print(idividual.genotype)
    print(population[0].fitness)
    print(f'------------------------------------------------')

-------------- GENERATION 1 --------------
CUT XOVER:
[True, False, True, False, False, True, False, True, True, False] + [False, True, True, False, False, True, False, True, True, True] -> [True, False, True, False, False, True, False, True, True, True]

MUTATION:
parent [True, False, False, True, True, False, False, False, False, False] -> [False, False, False, True, True, False, False, False, False, False]

CUT XOVER:
[True, False, False, True, False, True, True, True, False, True] + [False, True, False, True, False, False, False, True, False, True] -> [True, False, False, True, False, False, False, True, False, True]

CUT XOVER:
[False, False, False, False, False, False, False, False, False, True] + [True, False, True, True, False, True, True, True, False, False] -> [False, False, False, False, False, False, False, False, False, False]

CUT XOVER:
[True, False, True, True, False, True, True, True, False, False] + [True, True, True, False, True, False, False, True, False, False] -> 